# Augment data from TSV files to change team names and years

## Create dictionary for mapping team names and abbreviations

In [3]:
# Create team map and team array
team_map = {
    "Atlanta Hawks": 0,
    "Boston Celtics": 1,
    "Cleveland Cavaliers": 2,
    "New Orleans Pelicans": 3,
    "Chicago Bulls": 4,
    "Dallas Mavericks": 5,
    "Denver Nuggets": 6,
    "Golden State Warriors": 7,
    "Houston Rockets": 8,
    "Los Angeles Clippers": 9,
    "Los Angeles Lakers": 10,
    "Miami Heat": 11,
    "Milwaukee Bucks": 12,
    "Minnesota Timberwolves": 13,
    "Brooklyn Nets": 14,
    "New York Knicks": 15,
    "Orlando Magic": 16,
    "Indiana Pacers": 17,
    "Philadelphia 76ers": 18,
    "Phoenix Suns": 19,
    "Portland Trail Blazers": 20,
    "Sacramento Kings": 21,
    "San Antonio Spurs": 22,
    "Oklahoma City Thunder": 23,
    "Toronto Raptors": 24,
    "Utah Jazz": 25,
    "Memphis Grizzlies": 26,
    "Washington Wizards": 27,
    "Detroit Pistons": 28,
    "Charlotte Hornets": 29
}

team_array = [
"Atlanta Hawks",
"Boston Celtics",
"Cleveland Cavaliers",
"New Orleans Pelicans",
"Chicago Bulls",
"Dallas Mavericks",
"Denver Nuggets",
"Golden State Warriors",
"Houston Rockets",
"Los Angeles Clippers",
"Los Angeles Lakers",
"Miami Heat",
"Milwaukee Bucks",
"Minnesota Timberwolves",
"Brooklyn Nets",
"New York Knicks",
"Orlando Magic",
"Indiana Pacers",
"Philadelphia 76ers",
"Phoenix Suns",
"Portland Trail Blazers",
"Sacramento Kings",
"San Antonio Spurs",
"Oklahoma City Thunder",
"Toronto Raptors",
"Utah Jazz",
"Memphis Grizzlies",
"Washington Wizards",
"Detroit Pistons",
"Charlotte Hornets"]

# Check that array and dictionary are aligned properly
for i in range(len(team_array)):
    if i != team_map[team_array[i]]:
        print("Invalid!")

# Create abbreviation map and array
abbreviation_array = [
"ATL",
"BOS",
"CLE",
"NOP",
"CHI",
"DAL",
"DEN",
"GSW",
"HOU",
"LAC",
"LAL",
"MIA",
"MIL",
"MIN",
"BKN",
"NYK",
"ORL",
"IND",
"PHI",
"PHX",
"POR",
"SAC",
"SAS",
"OKC",
"TOR",
"UTA",
"MEM",
"WAS",
"DET",
"CHA"]

abbreviation_map = {}
for i in range(len(abbreviation_array)):
    abbreviation_map[abbreviation_array[i]] = i

print(len(team_array))
print(len(team_map))
print(len(abbreviation_array))
print(len(abbreviation_map))

# Check that team names, abbreviation and index maps all line up
for i in range(len(team_array)):
    print(str(i) + "," + team_array[i] + "," + str(team_map[team_array[i]]) + "," + abbreviation_array[i] + "," + str(abbreviation_map[abbreviation_array[i]]))
 

30
30
30
30
0,Atlanta Hawks,0,ATL,0
1,Boston Celtics,1,BOS,1
2,Cleveland Cavaliers,2,CLE,2
3,New Orleans Pelicans,3,NOP,3
4,Chicago Bulls,4,CHI,4
5,Dallas Mavericks,5,DAL,5
6,Denver Nuggets,6,DEN,6
7,Golden State Warriors,7,GSW,7
8,Houston Rockets,8,HOU,8
9,Los Angeles Clippers,9,LAC,9
10,Los Angeles Lakers,10,LAL,10
11,Miami Heat,11,MIA,11
12,Milwaukee Bucks,12,MIL,12
13,Minnesota Timberwolves,13,MIN,13
14,Brooklyn Nets,14,BKN,14
15,New York Knicks,15,NYK,15
16,Orlando Magic,16,ORL,16
17,Indiana Pacers,17,IND,17
18,Philadelphia 76ers,18,PHI,18
19,Phoenix Suns,19,PHX,19
20,Portland Trail Blazers,20,POR,20
21,Sacramento Kings,21,SAC,21
22,San Antonio Spurs,22,SAS,22
23,Oklahoma City Thunder,23,OKC,23
24,Toronto Raptors,24,TOR,24
25,Utah Jazz,25,UTA,25
26,Memphis Grizzlies,26,MEM,26
27,Washington Wizards,27,WAS,27
28,Detroit Pistons,28,DET,28
29,Charlotte Hornets,29,CHA,29


## Create function to augment data by updating team names in SQL queries

In [44]:
import random
import pandas as pd
import sqlite3 as sql

# Find team names in the sample
def find_teams_in_sample(sample, team_list):
    result = []
    for i in range(len(team_list)):
        if team_list[i] in sample:
            result.append(i)
    return result

# Get random number excluding the one already used
def get_random_excluding(floor, ceiling, excluded_number):
    number = random.randint(floor, ceiling)
    while number == excluded_number:
        number = random.randint(floor, ceiling)
    return number

def augment_dataframe(df, team_list, abbreviation_list, database):
    augmented_df = df.copy()
    for _, row in df.iterrows():
        team_idx = find_teams_in_sample(row["natural_query"], team_list)
        # Only do simple update if only one team detected 
        if len(team_idx) == 1:
            team_idx = team_idx[0]

            # Check if team name is used in SQL query
            if team_list[team_idx] in row["sql_query"]:
                # Create updated query with new team 
                new_team_name = team_list[get_random_excluding(0, 29, team_idx)]
                new_natural_query = row["natural_query"].replace(team_list[team_idx], new_team_name)
                new_sql_query = row["sql_query"].replace(team_list[team_idx], new_team_name)

                # Obtain result of running on sqlite database
                try:
                    database.execute(new_sql_query)
                    rows = database.fetchall()
                    if len(rows) == 1:
                        if len(rows[0]) == 2 and rows[0][1] == None:
                            result = str(rows[0][0])
                        else:
                            result = " | ".join(str(x) for x in rows[0]) 
                    else:
                        result = " | ".join(str(x) for x in rows)
                    # Append new row to augmented dataframe if result successful
                    new_row = pd.DataFrame([{'natural_query': new_natural_query, 'sql_query': new_sql_query, 'result': result}])
                    augmented_df = pd.concat([augmented_df, new_row], ignore_index=True)
                except:
                    pass

            # Check if abbreviation is in SQL query used instead
            elif abbreviation_list[team_idx] in row["sql_query"]:
                # Create updated query with new team 
                new_index = get_random_excluding(0, 29, team_idx)
                new_team_name = team_list[new_index]
                new_team_abbreviation = abbreviation_list[new_index]
                new_natural_query = row["natural_query"].replace(team_list[team_idx], new_team_name)
                new_sql_query = row["sql_query"].replace(abbreviation_list[team_idx], new_team_abbreviation)

                # Obtain result of running on sqlite database
                try:
                    database.execute(new_sql_query)
                    rows = database.fetchall()
                    if len(rows) == 1:
                        
                        if len(rows[0]) == 2 and rows[0][1] == None:
                            result = str(rows[0][0])
                        else:
                            result = " | ".join(str(x) for x in rows[0]) 
                    else:
                        result = " | ".join(str(x) for x in rows)
                    # Append new row to augmented dataframe if result successful
                    new_row = pd.DataFrame([{'natural_query': new_natural_query, 'sql_query': new_sql_query, 'result': result}])
                    augmented_df = pd.concat([augmented_df, new_row], ignore_index=True)
                except:
                    pass
    return augmented_df


## Test functions on small dataframe sample

In [47]:
# Load dataset
train_df = pd.read_csv("./train-data/sql_train.tsv", sep='\t')

# Display dataset info
print(f"Total dataset examples: {len(train_df)}")
#print(train_df.head())

# Setup sqlite database connection
connection = sql.connect('./nba-data/nba.sqlite')
cursor = connection.cursor()

# Test augmentation on sample of 3 rows
test_df = train_df.sample(n=3)
#for _, row in test_df.iterrows():
    #print(row)
#print()
#print()

# Run augmentation function and print output
augmented_df = augment_dataframe(test_df, team_array, abbreviation_array, cursor)
print("New Dataset Length:")
print(len(augmented_df))
print()
for _, row in augmented_df.iterrows():
    print(row["natural_query"])
    print(row["sql_query"])
    print(row["result"])
    print()

Total dataset examples: 1044
New Dataset Length:
6

What is the total free throws made by the Indiana Pacers at home?
SELECT SUM(ftm_home) as total_ftm  FROM game  WHERE team_name_home = 'Indiana Pacers';
39545.0

How many total rebounds did the Los Angeles Lakers grab in the 1985 season?
SELECT SUM(reb) AS total_rebounds FROM (     SELECT reb_home AS reb FROM game WHERE team_abbreviation_home = 'LAL' AND season_id = '21985'     UNION ALL     SELECT reb_away AS reb FROM game WHERE team_abbreviation_away = 'LAL' AND season_id = '21985' );
3655.0

How many home games did the Orlando Magic play in the 2013 season?
SELECT COUNT(*) FROM game WHERE team_name_home = 'Orlando Magic' AND season_id = '22013';
41.0

What is the total free throws made by the Denver Nuggets at home?
SELECT SUM(ftm_home) as total_ftm  FROM game  WHERE team_name_home = 'Denver Nuggets';
43821.0

How many total rebounds did the Miami Heat grab in the 1985 season?
SELECT SUM(reb) AS total_rebounds FROM (     SELECT reb